In [ ]:
# Librerías que vamos a usar
from google.colab import drive
from google.colab import files
import os
import re
import numpy as np
import pandas as pd
from collections import defaultdict
from itertools import groupby, zip_longest
import pickle
from collections import Counter
import matplotlib.pyplot as plt

# Sirve para conectar con el drive
drive.mount('/content/drive') #

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import json
import pandas as pd

# Cargar el JSON
with open('/content/drive/MyDrive/dataset_final.json', 'r') as f:
    data = json.load(f)

# Si es una lista de diccionarios:
df = pd.DataFrame(data)

# Ahora sí puedes usar .head()
df.head()
#df.info()
#df.iloc[0]['FFT_PCA_1']


max_V     rms_V    max_H1    rms_H1    max_H2    rms_H2  duration  \
0  0.000342  0.000052  0.000587  0.000111  0.000617  0.000107    321.68   
1  0.003967  0.000347  0.006399  0.000501  0.004988  0.000475    200.00   
2  0.000135  0.000023  0.000204  0.000028  0.000157  0.000026    323.79   
3  0.003166  0.000453  0.005030  0.000657  0.004669  0.000725     41.00   
4  0.000011  0.000002  0.000021  0.000003  0.000018  0.000003    180.80   

       zcr_V  dom_freq_V  centroid_V  ...  FFT_PCA_62  1 Stiker Slip (SS)  \
0   2.014362    0.000000    5.447156  ...    0.015319                True   
1   9.034548    0.781250   17.551070  ...    0.015314                True   
2   1.429895    0.195312    2.573894  ...    0.015312                True   
3  21.189954   14.062500   14.019404  ...    0.001835                True   
4   3.943366    0.195312   10.936094  ...    0.015316                True   

   2 Normal-Oblique (SO)  3 Reverse-Oblique (RO)   4-6    6-8  0-200  200-400  \
0                  False                   False  True  False  False    False   
1                  False                   False  True  False  False    False   
2                  False                   False  True  False  False    False   
3                  False                   False  True  False  False    False   
4                  False                   False  True  False  False    False   

   400-600  600-  
0    False  True  
1    False  True  
2    False  True  
3    False  True  
4    False  True  

[5 rows x 91 columns]

In [ ]:
# Primero, definimos qué columnas son las etiquetas one-hot
label_cols = [
    '1 Stiker Slip (SS)', '2 Normal-Oblique (SO)', '3 Reverse-Oblique (RO)',
    '4-6', '6-8', '0-200', '200-400', '400-600', '600-'
]

# Features: todas las columnas EXCEPTO las etiquetas
feature_cols = [c for c in df.columns if c not in label_cols]

# X = solo las features (float64)
X = df[feature_cols].values

# Y = las etiquetas multilabel (binario)
y = df[label_cols].astype(int).values  # Convertimos True/False a 0/1

print('Features shape:', X.shape)  # Debería ser [n_samples, 82]
print('Labels shape:', y.shape)    # Debería ser [n_samples, 9]


Features shape: (1674, 82)
Labels shape: (1674, 9)


In [ ]:
from sklearn.preprocessing import StandardScaler


scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

print('Scaled Features shape:', X_scaled.shape)


Scaled Features shape: (1674, 82)


In [ ]:
import torch
X_tensor = torch.tensor(X_scaled, dtype=torch.float32)
y_tensor = torch.tensor(y, dtype=torch.float32)  # multilabel → float para BCE


In [ ]:
pip install Lightning

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 819.0/819.0 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 89.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 84.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 50.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 89.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 961.5/961.5 kB 47.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
from torch.utils.data import TensorDataset, DataLoader, random_split, Subset
import lightning as L

class SeismicDataModule(L.LightningDataModule):
    def __init__(self, X_tensor, y_tensor, batch_size=64):
        super().__init__()
        self.X_tensor = X_tensor
        self.y_tensor = y_tensor
        self.batch_size = batch_size
        self.input_shape = X_tensor.shape[1]   # 82 features
        self.num_classes = y_tensor.shape[1]   # 9 labels

    def prepare_data(self):
        pass

    def setup(self, stage=None):
        full_dataset = TensorDataset(self.X_tensor, self.y_tensor)
        if stage == 'fit' or stage is None:
            train_size = int(0.8 * len(full_dataset))
            val_size = len(full_dataset) - train_size
            seed = torch.Generator().manual_seed(42)
            self.train_dataset, self.val_dataset = random_split(full_dataset, [train_size, val_size], generator=seed)
        if stage == 'test' or stage is None:
            self.test_dataset = full_dataset
        if stage == 'predict' or stage is None:
            self.predict_dataset = Subset(full_dataset, range(5))

    def train_dataloader(self):
        return DataLoader(self.train_dataset, batch_size=self.batch_size, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_dataset, batch_size=self.batch_size, shuffle=False)

    def test_dataloader(self):
        return DataLoader(self.test_dataset, batch_size=self.batch_size, shuffle=False)

    def predict_dataloader(self):
        return DataLoader(self.predict_dataset, batch_size=self.batch_size, shuffle=False)

dm = SeismicDataModule(X_tensor, y_tensor, batch_size=32)

#preparar los datasets (train/val/test/predict)
dm.setup()  # Si quieres preparar TODO
# o
# dm.setup(stage="fit")  # Solo preparar train/val



In [ ]:
train_loader = dm.train_dataloader()

for x_batch, y_batch in train_loader:
    print('X batch shape:', x_batch.shape)
    print('Y batch shape:', y_batch.shape)
    break


X batch shape: torch.Size([32, 82])
Y batch shape: torch.Size([32, 9])


In [ ]:
pip install torchmetrics


In [ ]:
import torch
import torch.nn as nn
import lightning as L
import torchmetrics

class SeismicMultilabelModel(L.LightningModule):
    def __init__(self, input_shape, num_classes, hidden_units, lambda_L2=0.0, lr=0.001):
        super().__init__()
        self.save_hyperparameters()

        layers = []
        layers.append(nn.Flatten())
        for units in hidden_units:
            layers.append(nn.Linear(input_shape, units))
            layers.append(nn.BatchNorm1d(units))
            layers.append(nn.LeakyReLU(negative_slope=0.01))
            input_shape = units
        layers.append(nn.Linear(input_shape, num_classes))  # logits
        self.classifier = nn.Sequential(*layers)

        #loss function
        self.criterion = nn.BCELoss()

        # metricas NO FUNCIONA HAMMING
        self.train_f1_micro = torchmetrics.F1Score(task="multilabel", num_labels=num_classes, average="micro")
        self.train_hamming = torchmetrics.HammingDistance(task="multilabel", num_labels=num_classes)

        self.val_f1_micro = torchmetrics.F1Score(task="multilabel", num_labels=num_classes, average="micro")
        self.val_hamming = torchmetrics.HammingDistance(task="multilabel", num_labels=num_classes)

    def forward(self, x):
        return self.classifier(x)

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.hparams.lr, weight_decay=self.hparams.lambda_L2)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        probs = torch.sigmoid(logits)
        loss = self.criterion(probs, y.float())

        #actualiza
        self.train_f1_micro.update(probs, y)
        self.train_hamming.update(probs, y)

        self.log('train_loss', loss, prog_bar=True)
        return loss

    def on_train_epoch_end(self):
        self.log('train_f1_micro', self.train_f1_micro.compute(), prog_bar=True)
        self.log('train_hamming', self.train_hamming.compute(), prog_bar=True)

        #reset de métricas
        self.train_f1_micro.reset()
        self.train_hamming.reset()

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        probs = torch.sigmoid(logits)
        loss = self.criterion(probs, y.float())

        self.log('val_loss', loss, prog_bar=True)

        #actualizar metricas
        self.val_f1_micro.update(probs, y)
        self.val_hamming.update(probs, y)

    def on_validation_epoch_end(self):
        self.log('val_f1_micro', self.val_f1_micro.compute(), prog_bar=True)
        self.log('val_hamming', self.val_hamming.compute(), prog_bar=True)

        #reset metricas
        self.val_f1_micro.reset()
        self.val_hamming.reset()


In [ ]:
 !pip install torchmetrics --upgrade


In [ ]:
import torchmetrics
print(torchmetrics.__version__)


1.7.1


In [ ]:
from torch.utils.data import TensorDataset, DataLoader, random_split

# 👉 Dataset completo
full_dataset = TensorDataset(X_tensor, y_tensor)

# 👉 Split 80% train / 20% test
train_size = int(0.8 * len(full_dataset))
test_size = len(full_dataset) - train_size
seed = torch.Generator().manual_seed(42)
train_dataset, test_dataset = random_split(full_dataset, [train_size, test_size], generator=seed)

# 👉 DataLoaders
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

# 👉 Instanciar modelo
model = SeismicMultilabelModel(
    input_shape=dm.input_shape,
    num_classes=dm.num_classes,
    hidden_units=[256, 128, 64],
    lambda_L2=1e-4,
    lr=0.001
)

# 👉 Trainer
trainer = L.Trainer(
    max_epochs=10,
    accelerator="gpu" if torch.cuda.is_available() else "cpu",
    devices=1
)

# 👉 Entrenar
trainer.fit(model, train_dataloaders=train_loader)

# 👉 Evaluar en test
trainer.validate(model, dataloaders=test_loader)


INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
/usr/local/lib/python3.11/dist-packages/lightning/pytorch/trainer/configuration_validator.py:70: You defined a `validation_step` but have no `val_dataloader`. Skipping val loop.
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 63.9 K | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance |

Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=10` reached.


Validation: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃      Validate metric      ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       val_f1_micro        │    0.6017601490020752     │
│        val_hamming        │    0.24013268947601318    │
│         val_loss          │    0.5263664126396179     │
└───────────────────────────┴───────────────────────────┘

[{'val_loss': 0.5263664126396179,
  'val_f1_micro': 0.6017601490020752,
  'val_hamming': 0.24013268947601318}]

In [ ]:
lambda_list = [0, 1e-5, 1e-4, 1e-3]
results_lambda = []

for lambda_L2 in lambda_list:
    print(f"\n🔍 Entrenando con lambda_L2 = {lambda_L2}")

    # 👉 Instanciar modelo con el lambda actual
    model = SeismicMultilabelModel(
        input_shape=dm.input_shape,
        num_classes=dm.num_classes,
        hidden_units=[256, 128, 64],  # Más robusto
        lambda_L2=lambda_L2,
        lr=0.001
    )

    # 👉 Trainer (ajustar epochs si quieres más)
    trainer = L.Trainer(
        max_epochs=30,
        accelerator="gpu" if torch.cuda.is_available() else "cpu",
        devices=1,
        enable_progress_bar=False,
        logger=False
    )

    # 👉 Entrenar con train/val del DataModule
    trainer.fit(model, dm)

    # 👉 Evaluar en test
    test_metrics = trainer.validate(model, dataloaders=dm.test_dataloader(), verbose=False)
    test_metrics[0]['lambda_L2'] = lambda_L2  # Agregar lambda al resultado
    results_lambda.append(test_metrics[0])

# 👉 Convertir resultados a DataFrame
df_lambda = pd.DataFrame(results_lambda)
print(df_lambda)


INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type              | Params | Mode 
-------------------------------------------------------------
0 | classifier     | Sequential        | 63.9 K | train
1 | criterion      | BCELoss           | 0      | train
2 | train_f1_micro | MultilabelF1Score | 0      | train
3 | val_f1_micro   | MultilabelF1Score | 0      | train
-------------------------------------------------------------
63.9 K    Trainable params
0         Non-trainable params
63.9 K    Total params
0.256     Total estimated model params size (MB)
15        Modules 


🔍 Entrenando con lambda_L2 = 0


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type              | Params | Mode 
-------------------------------------------------------------
0 | classifier     | Sequential        | 63.9 K | train
1 | criterion      | BCELoss           | 0      | train
2 | train_f1_micro | MultilabelF1Score | 0      | train
3 | val_f1_micro   | MultilabelF1Score | 0      | train
-------------------------------------------------------------
63.9 K    Trainable params
0         Non-trainable params


🔍 Entrenando con lambda_L2 = 1e-05


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type              | Params | Mode 
-------------------------------------------------------------
0 | classifier     | Sequential        | 63.9 K | train
1 | criterion      | BCELoss           | 0      | train
2 | train_f1_micro | MultilabelF1Score | 0      | train
3 | val_f1_micro   | MultilabelF1Score | 0      | train
-------------------------------------------------------------
63.9 K    Trainable params
0         Non-trainable params


🔍 Entrenando con lambda_L2 = 0.0001


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type              | Params | Mode 
-------------------------------------------------------------
0 | classifier     | Sequential        | 63.9 K | train
1 | criterion      | BCELoss           | 0      | train
2 | train_f1_micro | MultilabelF1Score | 0      | train
3 | val_f1_micro   | MultilabelF1Score | 0      | train
-------------------------------------------------------------
63.9 K    Trainable params
0         Non-trainable params


🔍 Entrenando con lambda_L2 = 0.001


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.


   val_loss  val_f1_micro  lambda_L2
0  0.260007      0.854894    0.00000
1  0.250132      0.858316    0.00001
2  0.263372      0.845964    0.00010
3  0.269212      0.834365    0.00100


In [ ]:
print(isinstance(model, L.LightningModule))


True


In [ ]:
kfrom pytorch_lightning import Trainer
from sklearn.model_selection import ParameterGrid

# 👉 Espacio de búsqueda (limitado para grid)
param_grid = {
    'hidden_units': [[32, 64, 16], [128, 64], [256, 128, 64]],
    'lr': [0.001, 0.0005],
    'lambda_L2': [0, 1e-5, 1e-4, 1e-3]
}

grid = ParameterGrid(param_grid)

results = []

for params in grid:
    print(f"\n🔍 Probando combinación: {params}")

    # 👉 Instanciar modelo con los parámetros actuales
    model = SeismicMultilabelModel(
        input_shape=dm.input_shape,
        num_classes=dm.num_classes,
        hidden_units=params['hidden_units'],
        lambda_L2=params['lambda_L2'],
        lr=params['lr']
    )

    # 👉 Entrenar el modelo
    trainer = L.Trainer(max_epochs=30, accelerator="gpu" if torch.cuda.is_available() else "cpu", devices=1, logger=False, enable_progress_bar=False)
    trainer.fit(model,dm)
    # 👉 Validar y capturar val_loss
    val_metrics = trainer.validate(model, dataloaders=dm.val_dataloader(), verbose=False)
    val_loss = val_metrics[0]['val_hamming']
    # 👉 Guardar resultados
    results.append((params, val_loss))

# 👉 Buscar la mejor combinación
best_params = sorted(results, key=lambda x: x[1])[0]
print(f"\nMejores parámetros: {best_params[0]}, Validation Loss: {best_params[1]}")


INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 6.2 K  | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance | 0      | train
4 | val_f1_micro   | MultilabelF1Score         | 0      | train
5 | val_hamming    | MultilabelHammingDistance | 0      | train
----------------------------------


🔍 Probando combinación: {'hidden_units': [32, 64, 16], 'lambda_L2': 0, 'lr': 0.001}


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 6.2 K  | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance | 0      | train
4 | val_f1_micro   | MultilabelF1Score         | 0      | train
5 | val


🔍 Probando combinación: {'hidden_units': [32, 64, 16], 'lambda_L2': 0, 'lr': 0.0005}


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 6.2 K  | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance | 0      | train
4 | val_f1_micro   | MultilabelF1Score         | 0      | train
5 | val

...


🔍 Probando combinación: {'hidden_units': [256, 128, 64], 'lambda_L2': 0.001, 'lr': 0.001}


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.
INFO:pytorch_lightning.utilities.rank_zero:Using default `ModelCheckpoint`. Consider installing `litmodels` package to enable `LitModelCheckpoint` for automatic upload to the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 63.9 K | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance | 0      | train
4 | val_f1_micro   | MultilabelF1Score         | 0      | train
5 | val


🔍 Probando combinación: {'hidden_units': [256, 128, 64], 'lambda_L2': 0.001, 'lr': 0.0005}


INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=30` reached.



Mejores parámetros: {'hidden_units': [256, 128, 64], 'lambda_L2': 1e-05, 'lr': 0.001}, Validation Loss: 0.23449420928955078


In [ ]:
## K - fold CV

from sklearn.model_selection import RepeatedKFold
from torch.utils.data import TensorDataset, DataLoader
import numpy as np
import pandas as pd

mejores_parametros = best_params[0]


# 👉 Configurar Repeated K-Fold
rkf = RepeatedKFold(n_splits=5, n_repeats=2, random_state=42)

# 👉 Guardar métricas por fold
results = []

# 👉 Loop de K-Fold
for fold, (train_idx, val_idx) in enumerate(rkf.split(X_tensor)):
    print(f"Fold {fold+1}")

    # 👉 Crear datasets por fold
    X_train_fold, y_train_fold = X_tensor[train_idx], y_tensor[train_idx]
    X_val_fold, y_val_fold = X_tensor[val_idx], y_tensor[val_idx]

    # 👉 Crear DataLoaders
    train_dataset = TensorDataset(X_train_fold, y_train_fold)
    val_dataset = TensorDataset(X_val_fold, y_val_fold)
    train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
    val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)

    # 👉 Instanciar el modelo Feedforward para cada fold
    model = SeismicMultilabelModel(
      input_shape=dm.input_shape,
      num_classes=dm.num_classes,
      hidden_units=mejores_parametros['hidden_units'],
      lambda_L2=mejores_parametros['lambda_L2'],
      lr=mejores_parametros['lr']
  )

    # 👉 Callbacks (solo ModelCheckpoint)
    checkpoint_callback = L.pytorch.callbacks.ModelCheckpoint(
        save_top_k=1, monitor="val_f1_micro", mode="min", save_last=False
    )
    callbacks = [checkpoint_callback]

    # 👉 Trainer por fold
    trainer = L.Trainer(
        max_epochs=50,
        callbacks=callbacks,
        accelerator="gpu" if torch.cuda.is_available() else "cpu",
        devices=1,
        enable_progress_bar=True,
        logger=False  # Desactivamos logger para evitar ruido en cada fold
    )

    # 👉 Entrenar modelo en el fold actual
    trainer.fit(model, train_dataloaders=train_loader, val_dataloaders=val_loader)

    # 👉 Evaluar en validación
    val_metrics = trainer.validate(model, val_loader, verbose=False)
    results.append(val_metrics[0])  # Guardar las métricas de este fold

# 👉 Convertir resultados a DataFrame
df_results = pd.DataFrame(results)
print(df_results)

# 👉 Calcular promedio y desviación estándar por métrica
summary = df_results.agg(['mean', 'std'])
print(summary)


INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
/usr/local/lib/python3.11/dist-packages/lightning/pytorch/callbacks/model_checkpoint.py:654: Checkpoint directory /content/checkpoints exists and is not empty.
INFO: 
  | Name           | Type                      | Params | Mode 
---------------------------------------------------------------------
0 | classifier     | Sequential                | 63.9 K | train
1 | criterion      | BCELoss                   | 0      | train
2 | train_f1_micro | MultilabelF1Score         | 0      | train
3 | train_hamming  | MultilabelHammingDistance | 0      | train
4 | val_f1_micro   | MultilabelF1Score         | 0      | train
5 | val_hamming    | MultilabelHammingDistance | 0      | train
---------------------------------------------------------------------
63.9 

Fold 1


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=50` reached.


Validation: |          | 0/? [00:00<?, ?it/s]

   val_loss  val_f1_micro  val_hamming
0  0.709179      0.640986     0.231841
1  0.822337      0.631253     0.237148
2  0.719901      0.627835     0.239469
3  0.668523      0.629515     0.238143
4  0.655038      0.650628     0.222222
5  0.815512      0.633840     0.231841
6  0.686100      0.638932     0.233167
7  0.726327      0.633897     0.237148
8  0.665680      0.646967     0.225871
9  0.804278      0.647151     0.224551
      val_loss  val_f1_micro  val_hamming
mean  0.727288      0.638100     0.232140
std   0.064372      0.008085     0.006114


In [ ]:
# escoger el mejor modelo
val_metrics = trainer.validate(model, dataloaders=dm.val_dataloader(), verbose=False)
print(f"Validation Loss: {val_metrics}")
test_metrics = trainer.validate(model, dataloaders=dm.test_dataloader(), verbose=False)
print(f"Test Loss: {test_metrics}")
train_metrics = trainer.validate(model, dataloaders=dm.train_dataloader(), verbose=False)
print(f"Train Loss: {train_metrics}")


Validation: |          | 0/? [00:00<?, ?it/s]

Validation Loss: [{'val_loss': 0.34134361147880554, 'val_f1_micro': 0.8652555346488953, 'val_hamming': 0.08656716346740723}]


Validation: |          | 0/? [00:00<?, ?it/s]

Test Loss: [{'val_loss': 0.2622937858104706, 'val_f1_micro': 0.8754995465278625, 'val_hamming': 0.08064514398574829}]


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/trainer/connectors/data_connector.py:476: Your `val_dataloader`'s sampler has shuffling enabled, it is strongly recommended that you turn shuffling off for val/test dataloaders.


Validation: |          | 0/? [00:00<?, ?it/s]

Train Loss: [{'val_loss': 0.24251657724380493, 'val_f1_micro': 0.8780363202095032, 'val_hamming': 0.0791635513305664}]
